# Task 4 

## Move and check all of the images 

In [1]:
import os
import shutil


In [ ]:
def filter_and_move_masks(masks_dir, masks_destination):
    """
    Filters masks ending with 'Corrected_root_mask.tif' and moves them to the masks_destination.
    """
    masks = os.listdir(masks_dir)
    os.makedirs(masks_destination, exist_ok=True)
    for mask in masks:
        if mask.endswith("Corrected_root_mask.tif"):
            mask_path = os.path.join(masks_dir, mask)
            dest_path = os.path.join(masks_destination, mask)
            shutil.move(mask_path, dest_path)
            print(f"Moved mask: {mask_path} to {dest_path}")


In [75]:
def match_and_move_images(masks_destination, images_dir, image_destination):
    """
    Matches masks in masks_destination with images in images_dir based on the first 15 characters
    and moves the matched images to image_destination.
    """
    masks = os.listdir(masks_destination)
    images = os.listdir(images_dir)
    os.makedirs(image_destination, exist_ok=True)

    # Extract mask bases (first 15 characters)
    mask_bases = {mask[:15] for mask in masks}
    print("Mask bases:", mask_bases)

    for image in images:
        image_base = image[:15]  # Compare only the first 15 characters
        if image_base in mask_bases:
            image_path = os.path.join(images_dir, image)
            dest_path = os.path.join(image_destination, image)
            if os.path.exists(image_path):
                shutil.move(image_path, dest_path)
                print(f"Moved image: {image_path} to {dest_path}")
            else:
                print(f"Image not found: {image_path}")
        else:
            print(f"No matching mask for image: {image}")


In [76]:
def validate_and_clean(masks_destination, image_destination):
    """
    Removes masks in masks_destination that do not have a corresponding image in image_destination.
    """
    masks = os.listdir(masks_destination)
    images = os.listdir(image_destination)

    # Extract the first 15 characters for correspondence
    image_bases = {image[:15] for image in images}

    # Remove unmatched masks
    for mask in masks:
        mask_base = mask[:15]
        if mask_base not in image_bases:
            mask_path = os.path.join(masks_destination, mask)
            os.remove(mask_path)
            print(f"Removed unmatched mask: {mask_path}")

    print("Cleanup complete: All masks correspond to images.")


In [ ]:
# Step 1: Filter and move valid masks
filter_and_move_masks(
    masks_dir=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\masks",
    masks_destination=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\masks_corrected"
)

# Step 2: Match masks with images and move corresponding images
match_and_move_images(
    masks_destination=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\masks_corrected",
    images_dir=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\images\train",
    image_destination=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\images_corrected"
)

# Step 3: Validate and clean unmatched masks
validate_and_clean(
    masks_destination=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\masks_corrected",
    image_destination=r"D:\Holland_Year_2\Block_B\2024-25b-fai2-adsai-PetarPaskalev232725\Y2B_23\images_corrected"
)


--- - - - - 

## Patches 

In [1]:
from patchify import patchify, unpatchify
import cv2
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
import os
import numpy as np
import cv2
from PIL import Image
import matplotlib.pyplot as plt

def load_image(image_path):
    """ Load an image in grayscale. """
    image = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    if image is None:
        print(f"Failed to load image: {image_path}")
        return None
    return image

def detect_edges(image, max_size=2800):
    """ Detect edges to find the approximate square Petri dish. """
    blurred_image = cv2.GaussianBlur(image, (51, 51), 0)

    # Compute horizontal and vertical gradients
    sobel_x = cv2.Sobel(blurred_image, cv2.CV_64F, 1, 0, ksize=5)
    sobel_y = cv2.Sobel(blurred_image, cv2.CV_64F, 0, 1, ksize=5)

    # Calculate the gradient magnitude
    gradient_magnitude = cv2.magnitude(sobel_x, sobel_y)

    # Threshold to identify strong edges
    _, edges = cv2.threshold(gradient_magnitude, 50, 255, cv2.THRESH_BINARY)
    edges = edges.astype(np.uint8)

    # Find contours to identify the Petri dish
    contours, _ = cv2.findContours(edges, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    # Assume the largest square-like contour is the Petri dish
    max_contour = max(contours, key=cv2.contourArea)
    x, y, w, h = cv2.boundingRect(max_contour)

    # Ensure the crop is a square, adjust dimensions as needed
    side_length = max(w, h)
    side_length = min(side_length, max_size)  # Clamp to max_size

    center_x, center_y = x + w // 2, y + h // 2
    half_side = side_length // 2

    # Define new bounding box that is a square centered at the original bounding box
    new_x = max(center_x - half_side, 0)
    new_y = max(center_y - half_side, 0)
    new_w = new_h = min(side_length, min(image.shape[1] - new_x, image.shape[0] - new_y))

    return new_x, new_x + new_w, new_y, new_y + new_h

def crop_image(image, edges, max_size=2800):
    """ Crop and resize the image to ensure dimensions are below the threshold. """
    left, right, top, bottom = edges
    cropped = image[top:bottom, left:right]

    # Resize if necessary
    if cropped.shape[1] > max_size or cropped.shape[0] > max_size:
        cropped = cv2.resize(cropped, (min(cropped.shape[1], max_size), min(cropped.shape[0], max_size)))

    return cropped

def process_and_crop_images(original_dir, tif_dir, output_original_dir, output_tif_dir):
    """ Process and crop images in original and corresponding TIFF files the same way. """
    processed_files = []
    skipped_files = []

    for filename in os.listdir(original_dir):
        if filename.endswith(".png"):
            original_image_path = os.path.join(original_dir, filename)

            # Match TIFF file using the first 15 characters of the filename
            base_name = filename[:53]
            corresponding_tif_path = None
            for tif_file in os.listdir(tif_dir):
                if tif_file.startswith(base_name) and tif_file.endswith(".tif"):
                    corresponding_tif_path = os.path.join(tif_dir, tif_file)
                    break

            if not corresponding_tif_path:
                print(f"Corresponding TIFF file not found for {filename}")
                skipped_files.append(filename)
                continue

            # Load original and corresponding TIFF images
            original_image = load_image(original_image_path)
            try:
                tif_image = np.array(Image.open(corresponding_tif_path))
            except Exception as e:
                print(f"Failed to load TIFF file: {corresponding_tif_path} - {e}")
                skipped_files.append(filename)
                continue

            if original_image is None or tif_image is None:
                skipped_files.append(filename)
                continue

            # Detect edges and crop
            edges = detect_edges(original_image)
            cropped_original = crop_image(original_image, edges)
            cropped_tif = crop_image(tif_image, edges)

            # Save cropped images
            output_original_path = os.path.join(output_original_dir, filename)
            output_tif_path = os.path.join(output_tif_dir, os.path.basename(corresponding_tif_path))

            cv2.imwrite(output_original_path, cropped_original)
            Image.fromarray(cropped_tif).save(output_tif_path)

            print(f"Processed and saved: {filename}")
            processed_files.append(filename)

    # Debugging information
    print("\nSummary of Processing:")
    print(f"Total files processed: {len(processed_files)}")
    print(f"Total files skipped: {len(skipped_files)}")
    if skipped_files:
        print("Skipped files:")
        for skipped in skipped_files:
            print(f"  - {skipped}")

# Define directories
original_dir = "D:/Holland_Year_2/Block_B/2024-25b-fai2-adsai-PetarPaskalev232725/Y2B_23/images_corrected"
tif_dir = "D:/Holland_Year_2/Block_B/2024-25b-fai2-adsai-PetarPaskalev232725/Y2B_23/masks_corrected"
output_original_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/train_images_cropped_2023"
output_tif_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/train_masks_cropped_2023"

# Ensure output directories exist
os.makedirs(output_original_dir, exist_ok=True)
os.makedirs(output_tif_dir, exist_ok=True)

# Process and crop images
process_and_crop_images(original_dir, tif_dir, output_original_dir, output_tif_dir)


Processed and saved: 001_43-18-ROOT1-2023-08-08_pvd_OD001_Col0_02-Fish Eye Corrected.png
Processed and saved: 001_43-6-ROOT1-2023-08-08_pvdCherry_OD001_Col0_04-Fish Eye Corrected.png
Processed and saved: 002_43-19-ROOT1-2023-08-08_pvd_OD001_Col0_01-Fish Eye Corrected.png
Processed and saved: 002_43-6-ROOT1-2023-08-08_pvd_OD001_Col0_01-Fish Eye Corrected.png
Processed and saved: 003_43-18-ROOT1-2023-08-08_pvdCherry_OD01_f6h1_01-Fish Eye Corrected.png
Processed and saved: 003_43-6-ROOT1-2023-08-08_pvd_OD0001_f6h1_03-Fish Eye Corrected.png
Processed and saved: 004_43-11-ROOT1-2023-08-08_pvdCherry_OD0001_f6h1_03-Fish Eye Corrected.png
Processed and saved: 004_43-17-ROOT1-2023-08-08_pvd_OD001_f6h1_04-Fish Eye Corrected.png
Processed and saved: 005_43-18-ROOT1-2023-08-08_pvd_OD001_Col0_05-Fish Eye Corrected.png
Processed and saved: 005_43-2-ROOT1-2023-08-08_control_pH7_-Fe+B_col0_04-Fish Eye Corrected.png
Processed and saved: 006_43-17-ROOT1-2023-08-08_mock_pH5_f6h1_02-Fish Eye Corrected.png

In [4]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from patchify import patchify
import os

# Define directories
image_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/train_images_cropped_2023"
mask_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/train_masks_cropped_2023"

# Output directories
output_image_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/dataset/train_images/train"
output_mask_dir = "D:/Holland_Year_2/Block_B/Task5_Patches/dataset/train_masks/train"

# Ensure output directories exist
os.makedirs(output_image_dir, exist_ok=True)
os.makedirs(output_mask_dir, exist_ok=True)

# Patch size and padding function
def padder(image, patch_size):
    """ Pad an image to make its dimensions divisible by the patch size. """
    h, w = image.shape[:2]
    height_padding = ((h // patch_size) + 1) * patch_size - h
    width_padding = ((w // patch_size) + 1) * patch_size - w

    top_padding = int(height_padding / 2)
    bottom_padding = height_padding - top_padding
    left_padding = int(width_padding / 2)
    right_padding = width_padding - left_padding

    padded_image = cv2.copyMakeBorder(image, top_padding, bottom_padding, left_padding, right_padding, cv2.BORDER_CONSTANT, value=[0, 0, 0])
    return padded_image

patch_size = 256

# Set a limit for the number of images to process

processed_count = 0

# Debugging: Print filenames in both directories
print("Image files:")
image_files = os.listdir(image_dir)
print(image_files)

print("Mask files:")
mask_files = os.listdir(mask_dir)
print(mask_files)

# Process images and masks
for filename in image_files:
    if filename.endswith(".png") :
        print(f"Processing file: {filename}")

        image_path = os.path.join(image_dir, filename)
        mask_path = None
        for mask_file in mask_files:
            if mask_file[:53] == filename[:53]:
                mask_path = os.path.join(mask_dir, mask_file)
                break

        if not mask_path or not os.path.exists(mask_path):
            print(f"Mask file not found for {filename}. Skipping.")
            continue

        # Read images
        image = cv2.imread(image_path)
        mask = cv2.imread(mask_path, cv2.IMREAD_UNCHANGED)  # Grayscale for masks

        if image is None or mask is None:
            print(f"Error reading image or mask for {filename}. Skipping.")
            continue

        # Pad images and masks
        padded_image = padder(image, patch_size)
        padded_mask = padder(mask, patch_size)

        # Patchify
        image_patches = patchify(padded_image, (patch_size, patch_size, 3), step=128)
        mask_patches = patchify(padded_mask, (patch_size, patch_size), step=128)

        # Save patches
        for i in range(image_patches.shape[0]):
            for j in range(image_patches.shape[1]):
                image_patch = image_patches[i, j, 0]
                mask_patch = mask_patches[i, j]

                # Create unique filenames for patches
                image_patch_filename = f"{filename[:-4]}_patch_{i}_{j}.png"
                mask_patch_filename = f"{filename[:-4]}_patch_{i}_{j}.tif"

                # Save patches
                cv2.imwrite(os.path.join(output_image_dir, image_patch_filename), image_patch)
                cv2.imwrite(os.path.join(output_mask_dir, mask_patch_filename), mask_patch)

                print(f"Finished processing {filename}. Total processed: {processed_count}")




Image files:
['001_43-18-ROOT1-2023-08-08_pvd_OD001_Col0_02-Fish Eye Corrected.png', '001_43-6-ROOT1-2023-08-08_pvdCherry_OD001_Col0_04-Fish Eye Corrected.png', '002_43-19-ROOT1-2023-08-08_pvd_OD001_Col0_01-Fish Eye Corrected.png', '002_43-6-ROOT1-2023-08-08_pvd_OD001_Col0_01-Fish Eye Corrected.png', '003_43-18-ROOT1-2023-08-08_pvdCherry_OD01_f6h1_01-Fish Eye Corrected.png', '003_43-6-ROOT1-2023-08-08_pvd_OD0001_f6h1_03-Fish Eye Corrected.png', '004_43-11-ROOT1-2023-08-08_pvdCherry_OD0001_f6h1_03-Fish Eye Corrected.png', '004_43-17-ROOT1-2023-08-08_pvd_OD001_f6h1_04-Fish Eye Corrected.png', '005_43-18-ROOT1-2023-08-08_pvd_OD001_Col0_05-Fish Eye Corrected.png', '005_43-2-ROOT1-2023-08-08_control_pH7_-Fe+B_col0_04-Fish Eye Corrected.png', '006_43-17-ROOT1-2023-08-08_mock_pH5_f6h1_02-Fish Eye Corrected.png', '006_43-6-ROOT1-2023-08-08_pvdCherry_OD001_Col0_01-Fish Eye Corrected.png', '007_43-18-ROOT1-2023-08-08_pvdCherry_OD001_Col0_05-Fish Eye Corrected.png', '007_43-6-ROOT1-2023-08-08_moc